In [25]:
import matplotlib.pyplot as plt
import numpy as np
import random 
from deap import base
from deap import creator
from deap import tools
import math

In [26]:
# Basic figures
acc_num = 100 #零件个数
type_acc = 8 #零件种类
step_num = 2 #工序数
group_num = math.ceil(math.pow(type_acc,1/step_num))
acc_bad_rate = [0.1,0.1,0.1,0.1,0.1,0.1,0.1,0.1]
acc_buy_price = [2,8,12,2,8,12,8,12]
acc_check_price = [1,1,2,1,1,2,1,2]
group_num

def calculate_half_num(step_num,group_num):
    result = 0
    for i in range(1, step_num):
        result += group_num**i
    return result

half_num = calculate_half_num(step_num,group_num)
half_check_price = [0,4,4,4] #半成品检测价， 是否需要增加数组长度方便计算
half_check_price
half_load_price = [0,8,8,8]
half_seperate_price = [0,6,6,6]
half_bad_rate = [0,0.1,0.1,0.1]
product_sale_price = 200
product_check_price = 6
product_bad_rate = 0.1
product_seperate_price = 10
product_load_price = 8
product_change_price = 40

In [27]:
# Fitness Function
creator.create("FitnessMulti",base.Fitness,weights=(0.02,0.8,-0.13))
creator.create("Individual",list,fitness=creator.FitnessMulti)

def calculate_individual_size():
    return type_acc + half_num*2 + 2 #individual构成[零件检修type_acc,半成品检修half_num，半成品拆分half_num，成品检修1,成品拆分1]

IND_SIZE = calculate_individual_size()
toolbox = base.Toolbox()
toolbox.register("attr_binary",random.randint,0,1)
toolbox.register("individual",tools.initRepeat,creator.Individual,toolbox.attr_binary,n=IND_SIZE)
#check
ind1 = toolbox.individual()
print(ind1)
IND_SIZE


[0, 1, 1, 0, 0, 1, 0, 1, 1, 0, 0, 0, 0, 1, 0, 1]


16

In [28]:
# Population
toolbox.register("population",tools.initRepeat,list,toolbox.individual)
pop = toolbox.population(n=5)
print(pop)

[[1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0], [1, 1, 0, 1, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 1, 0], [0, 0, 0, 1, 1, 1, 1, 0, 0, 0, 1, 0, 1, 1, 0, 1], [1, 0, 1, 1, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 1, 1], [1, 1, 0, 1, 1, 1, 0, 1, 0, 1, 0, 0, 0, 1, 0, 1]]


In [29]:
# Evaluation
def evaluate(individual):
# 零件到半成品
    acc2half_buy_cost = acc_num * sum(acc_buy_price)
    acc2half_check_cost = 0
    for i in range(type_acc):
        acc2half_check_cost += acc_check_price[i] * individual[i]
    acc2half_check_cost *= acc_num
    A = np.zeros((type_acc + 1, type_acc + 1)) #代表每个阶段的不合格品
    B = np.zeros((type_acc + 1, type_acc + 1)) #代表每个阶段的合格品
    M = np.zeros((type_acc + 1, type_acc + 1)) #代表每个阶段拆解可以节省的费用
    half_num_1 = group_num ** (step_num - 1)
    for i in range(1,half_num_1 + 1):
        start_index = i * group_num - group_num
        end_index = i * group_num
        max_result = -math.inf
        min_result = math.inf
        for j in range(start_index,end_index):
            #有可能最后一个半成品合成零件数不够
            if j >= type_acc:
                break
            max_result = max(max_result,acc_bad_rate[j] * (1 - individual[j]))
            min_result = min(min_result,1 - acc_bad_rate[j] * individual[j])
        A[1][i] = max_result * acc_num
        B[1][i] = min_result * acc_num
    acc2half_load_cost = 0
    acc2half_seperate_cost = 0
    half1_check_cost = 0
    for i in range(1, half_num_1 + 1):
        acc2half_load_cost += half_load_price[i] * (A[1][i] + B[1][i])
        acc2half_seperate_cost += individual[type_acc + i - 1] * half_seperate_price[i] * individual[type_acc + half_num + i - 1] * (A[1][i] + B[1][i] * half_bad_rate[i])
        half1_check_cost += half_check_price[i] * individual[type_acc + half_num + i - 1] * (A[1][i] + B[1][i])
    # 零件到半成品，拆解能省下的费用
    acc2half_save_cost = 0
    for i in range(1, half_num_1 + 1):
        start_index = i * group_num - group_num
        end_index = i * group_num
        acc_sum = 0
        for j in range(start_index,end_index):
            #有可能最后一个半成品合成零件数不够
            if j >= type_acc:
                break
            acc_sum += acc_buy_price[j]
            bad_ones = min(B[1][i],acc_num * acc_bad_rate[j] * (1 - individual[j])) * acc_buy_price[j]
        M[1][i] = (B[1][i] * half_bad_rate[i] * acc_sum + bad_ones ) * individual[type_acc + i - 1]
        acc2half_save_cost += M[1][i] * individual[type_acc + half_num + i - 1]
# 半成品到半成品,递推关系

    def calculate_past_half_num(i,group_num, step_num):
        result = 0
        for j in range(1,i):
            result += group_num ** (step_num - j)
        return result

    
    half_check_sum = 0
    half_separate_sum = 0
    half_load_sum = 0
    half_save_cost = 0

    for i in range(2,step_num):
        half_num_i = group_num ** (step_num - i)
        past_half_num = calculate_past_half_num(i - 1,group_num,step_num) #上一步已经计算的半成品数
        temp_check_sum = 0
        temp_load_sum = 0
        temp_separate_sum = 0
        temp_save_cost = 0
        for j in range(1,half_num_i + 1):
            start_index = j * group_num - group_num +1
            end_index = j * group_num
            max_result = -math.inf
            min_result = math.inf
            M_sum = 0
            for k in range(start_index,end_index):
                if k >= half_num_i * group_num:
                    break
                max_result = max(max_result, (A[i-1][k] + B[i-1][k] * half_bad_rate[past_half_num + k] ) * (1 - individual[type_acc + past_half_num + k - 1]))
                min_result = min(min_result, B[i-1][k] * (1 - half_bad_rate[past_half_num + k]))
                M_sum += M[i-1][k]
            A[i][j] = max_result
            B[i][j] = min_result
            temp_check_sum += (A[i][j] + B[i][j]) * half_check_price[past_half_num + half_num_i * group_num + j] * individual[type_acc + past_half_num + half_num_i * group_num + j - 1]
            temp_load_sum += (A[i][j] + B[i][j]) * half_load_price[past_half_num + half_num_i * group_num + j]
            temp_separate_sum += individual[type_acc + past_half_num + half_num_i * group_num + j - 1] * half_seperate_price[past_half_num + half_num_i * group_num + j] * individual[type_acc + past_half_num + half_num_i * group_num + half_num + j - 1] * (A[i][j] + B[i][j] * half_bad_rate[past_half_num + half_num_i * group_num + j])
            start_index = j * group_num ** i - group_num ** i
            end_index = j * group_num ** i
            tt_sum = 0
            for k in range(start_index,end_index):
                if k >= type_acc:
                    break
                tt_sum += acc_buy_price[k]
            M[i][j] = (M_sum + tt_sum * B[i][j] * half_bad_rate[past_half_num + half_num_i * group_num + j] * individual[type_acc + past_half_num + half_num_i * group_num + j - 1])
            temp_save_cost += M[i][j] * individual[type_acc + past_half_num + half_num_i * group_num + half_num + j - 1]
        half_check_sum += temp_check_sum
        half_load_sum += temp_load_sum
        half_separate_sum += temp_separate_sum
        half_save_cost += temp_save_cost
    
# 半成品到成品
    past_half_num = calculate_past_half_num(step_num - 1,group_num,step_num)
    max_result = -math.inf
    min_result = math.inf
    M_sum = 0
    for i in range(1, group_num + 1):
        max_result = max(max_result, (A[step_num - 1][i] + B[step_num - 1][i] * half_bad_rate[past_half_num + i]) * (1 - individual[type_acc + past_half_num + i - 1]))
        min_result = min(min_result, B[step_num - 1][i] * (1 - half_bad_rate[past_half_num + i]))
        M_sum += M[step_num - 1][i]
    A[step_num][1] = max_result
    B[step_num][1] = min_result
    product_check_cost = (A[step_num][1] + B[step_num][1]) * product_check_price * individual[-2]
    product_load_cost = (A[step_num][1] + B[step_num][1]) * product_load_price
    product_separate_cost = individual[-2] * product_seperate_price * individual[-1] * (A[step_num][1] + B[step_num][1] * product_bad_rate)
    product_save_cost = (M_sum + acc2half_buy_cost * B[step_num][1] * product_bad_rate * individual[type_acc + past_half_num] ) * individual[-1]
    product_change_cost = product_change_price * individual[-2] * (A[step_num][1] + B[step_num][1] * product_bad_rate)
    product_sale = product_sale_price * (A[step_num][1] + B[step_num][1]) * (1 - product_bad_rate * individual[-1])
    print(A)
    print(M)
    

# 总费用
    total_cost = acc2half_buy_cost + acc2half_check_cost + acc2half_load_cost + acc2half_seperate_cost + half1_check_cost - acc2half_save_cost + half_check_sum + half_load_sum + half_separate_sum - half_save_cost + product_check_cost + product_load_cost + product_separate_cost - product_save_cost + product_change_cost
    profit = product_sale - total_cost

# 总检验次数
    total_check = acc_num * sum(individual[:type_acc]) + sum(individual[-2:])
    for i in range(1,step_num):
        half_num_i = group_num ** (step_num - i)
        for j in range(1,half_num_i + 1):
            step = calculate_past_half_num(i,group_num,step_num)
            total_check += (A[i][j] + B[i][j]) * individual[type_acc + step + j - 1] + (A[i][j] + B[i][j] * half_bad_rate[calculate_past_half_num(i,group_num,step_num) + j]) * individual[type_acc + step + half_num + j - 1]

# 成品合格总数
    total_product = B[step_num][1] * (1 - product_bad_rate) 
    return total_product, profit, total_check

In [30]:
num_population = 10
N_GEN = 1000
toolbox.register("mate", tools.cxTwoPoint)
toolbox.register("mutate", tools.mutFlipBit, indpb=0.05)
toolbox.register("select", tools.selNSGA2)
toolbox.register("evaluate", evaluate)

pop = toolbox.population(n=num_population)

fitnesses = list(map(toolbox.evaluate, pop))
for ind, fit in zip(pop, fitnesses):
    ind.fitness.values = fit

CXPB, MUTPB = 0.5, 0.2

for g in range(N_GEN):
    # 选择并克隆个体
    offspring = toolbox.select(pop, len(pop))
    offspring = list(map(toolbox.clone, offspring))
    for child1, child2 in zip(offspring[::2], offspring[1::2]):
        if random.random() < CXPB:
            toolbox.mate(child1, child2)
            del child1.fitness.values
            del child2.fitness.values
    for mutant in offspring:
        if random.random() < MUTPB:
            toolbox.mutate(mutant)
            del mutant.fitness.values

    invalid_ind = [ind for ind in offspring if not ind.fitness.valid]
    if invalid_ind:
        fitnesses = map(toolbox.evaluate, invalid_ind)
        for ind, fit in zip(invalid_ind, fitnesses):
            ind.fitness.values = fit

    # 将父代与子代合并，选择下一代
    pop = toolbox.select(offspring + pop, num_population)

    fits = [ind.fitness.values[0] for ind in pop]
    length = len(pop)
    mean = sum(fits) / length
    sum2 = sum(x*x for x in fits)
    std = abs(sum2 / length - mean**2)**0.5
    print("Generation %i: Min %s Max %s Avg %s Std %s" % (g, min(fits), max(fits), mean, std))
    pareto_front = tools.sortNondominated(pop, len(pop), first_front_only=True)[0]
    print("Pareto Front (Generation %i):" % g)
    for ind in pareto_front:
        print(ind, ind.fitness.values)
    best_individual = max(pop, key=lambda ind: ind.fitness.values)
    print("Best individual (Generation %i): %s, Fitness: %s" % (g, best_individual, best_individual.fitness.values))
    





[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0. 10. 10. 10.  0.  0.  0.  0.  0.]
 [ 0. 19.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]]
[[  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0. 198. 318.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]
 [  0.   0.   0.   0.   0.   0.   0.   0.   0.]]
[[ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0. 10. 10. 10.  0.  0.  0.  0.  0.]
 [ 0. 19.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0.  0.  0.  0.  0.]
 [ 0.  0.  0.  0.  0